In [6]:
import tensorflow as tf
from collections import defaultdict
from pathlib import Path

In [2]:
tfrecord_file = "/home/ape/repos/road_quality/testing_interactive_tfexample.tfrecord-00000-of-00150"

In [3]:
raw_dataset = tf.data.TFRecordDataset(tfrecord_file)


E0000 00:00:1755668299.505305   13294 cuda_executor.cc:1309] INTERNAL: CUDA Runtime error: Failed call to cudaGetRuntimeVersion: Error loading CUDA libraries. GPU will not be used.: Error loading CUDA libraries. GPU will not be used.
W0000 00:00:1755668299.512124   13294 gpu_device.cc:2342] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


In [4]:
for raw_record in raw_dataset.take(1):
    print("Raw record:")
    print(raw_record)

Raw record:
tf.Tensor(b'\n\xee\xa0t\n\xe3\xfc\x15\n\x15roadgraph_samples/dir\x12\xc8\xfc\x15\x12\xc4\xfc\x15\n\xc0\xfc\x15H\xa0!>{\xca|?\x8cnk:b\x94!>\xf5\xca|?APc:P\x95!>\xeb\xca|?\x8cnk:\x12\xa3!>_\xca|?APc:\xa8\xbd!>O\xc9|?\x8cnk:\x12\xe5!>\xbb\xc7|?APc:P\x19">\xa3\xc5|?\x8cnk:aZ">\x07\xc3|?APc:D\xa8">\xe6\xbf|?\x8dnk:\xfa\x02#>?\xbc|?BPc:\x82j#>\x11\xb8|?\x8dnk:\xdb\xde#>[\xb3|?\x8dnk:\x05`$>\x1e\xae|?BPc:\xfe\xed$>U\xa8|?\x8dnk:\xc6\x88%>\x02\xa2|?BPc:\\0&>!\x9b|?\x8dnk:\xbe\xe4&>\xb2\x93|?BPc:\x9a\xa5\'>\xb6\x8b|?\xa6\x18k:bh(>\x9d\x83|?\xfd\xc2j:D")>\xd9{|?\x9c\xaab:\xa4\xd2)>rt|?\xfd\xc2j:\x84y*>km|?\x9c\xaab:\xe4\x16+>\xc3f|?\xfd\xc2j:\xc5\xaa+>|`|?\xfd\xc2j:(5,>\x98Z|?\x9c\xaab:\x0c\xb6,>\x16U|?\xfd\xc2j:t-->\xf9O|?\xfd\xc2j:`\x9b->AK|?\x9d\xaab:\xce\xff->\xedF|?\xfd\xc2j:\xc2Z.>\x01C|?\x9d\xaab:;\xac.>{?|?\xfd\xc2j:8\xf4.>\\<|?\xfd\xc2j:\xbc2/>\xa79|?\x9d\xaab:\xc5g/>X7|?\xfd\xc2j:U\x93/>s5|?\xfd\xc2j:l\xb5/>\xf83|?\x9d\xaab:\x08\xce/>\xe52|?\xfd\xc2j:+\xdd/><2|?\xfd\xc2j:\x

2025-08-19 22:38:21.915115: I tensorflow/core/kernels/data/tf_record_dataset_op.cc:390] TFRecordDataset `buffer_size` is unspecified, default to 262144
2025-08-19 22:38:21.942371: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


In [7]:
def describe_tfrecord(path, max_examples=5):
    dataset = tf.data.TFRecordDataset(str(path), compression_type="")
    feature_stats = defaultdict(dict)

    for raw in dataset.take(max_examples):
        ex = tf.train.Example()
        ex.ParseFromString(raw.numpy())

        for k, feat in ex.features.feature.items():
            if feat.HasField("bytes_list"):
                dtype = "bytes"
                val   = feat.bytes_list.value[0]
            elif feat.HasField("float_list"):
                dtype = "float"
                val   = feat.float_list.value[0]
            elif feat.HasField("int64_list"):
                dtype = "int64"
                val   = feat.int64_list.value[0]
            else:
                dtype = "UNKNOWN"
                val = None
            # keep first example of each feature
            if "dtype" not in feature_stats[k]:
                feature_stats[k]["dtype"] = dtype
                feature_stats[k]["example_value"] = val

    print(f"Found {len(feature_stats)} distinct feature keys "
          f"in first {max_examples} examples:\n")
    for k, info in feature_stats.items():
        print(f"  {k:<40}  {info['dtype']:<6}  sample: {info['example_value']}")
        
describe_tfrecord(tfrecord_file, max_examples=10)

Found 72 distinct feature keys in first 10 examples:

  state/current/vel_yaw                     float   sample: -0.1813240796327591
  state/past/width                          float   sample: 2.1636757850646973
  state/past/valid                          int64   sample: 1
  state/future/length                       float   sample: -1.0
  state/future/height                       float   sample: -1.0
  scenario/id                               bytes   sample: b'317c41438463fbc1'
  traffic_light_state/past/valid            int64   sample: 0
  traffic_light_state/future/valid          int64   sample: 0
  traffic_light_state/future/state          int64   sample: -1
  state/id                                  float   sample: 17.0
  traffic_light_state/future/id             int64   sample: -1
  roadgraph_samples/dir                     float   sample: 0.15783798694610596
  roadgraph_samples/xyz                     float   sample: -535.9067993164062
  state/objects_of_interest              

2025-08-19 22:38:39.681964: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
